In [16]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
from tqdm import tqdm
from math import ceil
import json
import re
import csv
import copy

In [2]:
# Raw headers string with HTTP headers required for the request
headers = """Host: www.edeka24.de
User-Agent: Mozilla/5.0 (Windows NT 10.0; Win64; x64; rv:121.0) Gecko/20100101 Firefox/121.0
Accept: text/html, */*; q=0.01
Accept-Language: en-US,en;q=0.5
Accept-Encoding: gzip, deflate, br
X-Requested-With: XMLHttpRequest
Connection: keep-alive
Referer: https://www.edeka24.de/Lebensmittel/Kaffee-Tee/?force_sid=k21t737cnfp5i6jerlb7tn064o
Cookie: language=0; sid=k21t737cnfp5i6jerlb7tn064o; sid_key=oxid; emos_jcsid=AYym_48rhFJgWOtTvoIa_BjOIZFlmxc1:t:1:0; _gcl_au=1.1.1298146631.1703608826
Sec-Fetch-Dest: empty
Sec-Fetch-Mode: cors
Sec-Fetch-Site: same-origin
Sec-GPC: 1
TE: trailers""".split('\n')

# Convert the raw headers string into a dictionary
# The split function breaks each line into a list element, 
# and then we create a dictionary by splitting each line at the first ':'
headers = {a.split(':')[0]: a.replace(a.split(':')[0] + ': ', '') for a in headers}


In [3]:
# When getting the homepage link it does not read the html but any type of category can be chosen to scrape the Edeka24
url = 'https://www.edeka24.de/Lebensmittel/Kaffee-Tee/' 

# Send a GET request to the URL with the headers
resp = requests.get(url, headers=headers)

# Parse the response text with BeautifulSoup
soup = BeautifulSoup(resp.text, 'html.parser')

In [4]:
# Initialize an empty list to store category links
cat_links = []

# Find all list items with the class 'nav-item-mobile is-level-2'
# These correspond to the product categories
for all_product_categories in soup.find_all(name='li', class_='nav-item-mobile is-level-2'):
    # Get the attributes of the anchor tag within each list item
    link_dics = all_product_categories.find('a').attrs
    
    # Check if 'data-link' attribute is present and append it to cat_links
    if 'data-link' in link_dics:
        cat_links.append(link_dics['data-link'])
    # Otherwise, check for 'href' attribute and append it to cat_links
    elif 'href' in link_dics:
        cat_links.append(link_dics['href'])

# Combine the main URL with the first 28 category links
categories = [url] + cat_links[0:28]

# Print the list of category URLs (optional)
# print(categories)


['https://www.edeka24.de/Lebensmittel/Kaffee-Tee/',
 'https://www.edeka24.de/Lebensmittel/Getraenke/',
 'https://www.edeka24.de/Lebensmittel/Backen-Desserts/',
 'https://www.edeka24.de/Lebensmittel/Fruehstueck-Snacks/',
 'https://www.edeka24.de/Lebensmittel/Wuerzmittel-Bruehen/',
 'https://www.edeka24.de/Lebensmittel/Sossen/',
 'https://www.edeka24.de/Lebensmittel/Beilagen/',
 'https://www.edeka24.de/Lebensmittel/Konserven/',
 'https://www.edeka24.de/Lebensmittel/Suess-Salzig/',
 'https://www.edeka24.de/Lebensmittel/Fertiggerichte/',
 'https://www.edeka24.de/Lebensmittel/Internationales/',
 'https://www.edeka24.de/Bio-Produkte/Bio-Marken/',
 'https://www.edeka24.de/Bio-Produkte/Lebensmittel-von-Alnatura/',
 'https://www.edeka24.de/Bio-Produkte/Fruehstuecksartikel-von-Alnatura/',
 'https://www.edeka24.de/Bio-Produkte/Getraenke-von-Alnatura/',
 'https://www.edeka24.de/Wein-Spirituosen/Rotwein/',
 'https://www.edeka24.de/Wein-Spirituosen/Weisswein/',
 'https://www.edeka24.de/Wein-Spirituo

In [5]:
all_links = []

# Initialize an empty list to store all product links
all_links = []

# Iterate over each category URL
for url in categories[:]:
    # Send a GET request to the first page of each category
    resp = requests.get(url + str(0), headers=headers)
    # Parse the HTML content of the first page
    soup = BeautifulSoup(resp.text, 'html.parser')
    # Extract product links from the first page
    links = [a.find('a').attrs['href'] for a in soup.find_all(class_='product-details')]
    # Calculate the total number of pages in the category
    pages = ceil(int(soup.find(class_='category-amount-articles').text.split(' ')[0]) / 30)

    # Iterate over each subsequent page in the category
    for p in tqdm(range(1, pages)):
        # Send a GET request to each page
        resp = requests.get(url + str(p), headers=headers)
        # Parse the HTML content of the page
        soup = BeautifulSoup(resp.text, 'html.parser')
        # Extract product links from the page and add them to the list
        links.extend([a.find('a').attrs['href'] for a in soup.find_all(class_='product-details')])

    # Extend the all_links list with the links from the current category
    all_links.extend(links)


100%|██████████| 4/4 [00:07<00:00,  1.98s/it]
0it [00:00, ?it/s]
0it [00:00, ?it/s]
0it [00:00, ?it/s]


In [6]:
# Initialize an empty list to store all product attributes
all_attrs = []

# Iterate over each product link
for l in tqdm(all_links[:]):
    # Send a GET request to the product page
    resp = requests.get(l, headers=headers)
    # Parse the HTML content of the product page
    soup = BeautifulSoup(resp.text, 'html.parser')
    
    # Initialize a dictionary to store attributes of the product
    attrs = {}
    
    # Placeholder for product ID (if needed in future)
    attrs['id'] = ''

    # Try to extract the product name
    try:
        attrs['name'] = soup.find('h1').text.strip()
    except:
        # If the name is not found, append the link and continue
        all_attrs.append({'link': l})
        pass

    # Placeholder for product brand (if needed in future)
    attrs['brand'] = ''

    # Initialize a list to store product descriptions
    product_desc = []
    
    # Extract product description details
    for listing in soup.find(id='description').find_all(class_='listing'):
        key = listing.text.strip().split(':')[0]
        if key == 'Zutatenverzeichnis':
            attrs["ingredients"] = re.sub(r'[\s]+', ' ', listing.text.replace(key + ':', '').strip())
        else:
            product_desc.append(re.sub(r'[\s]+', ' ', listing.text.strip()))

    # Extract product category and sub-category
    attrs['category'] = soup.find('div', class_='breadcrumb').find_all('a')[1].text.strip()
    try:
        attrs['sub-category'] = soup.find('div', class_='breadcrumb').find_all('a')[2].text.strip()
    except:
        pass

    # Placeholder for allergens and labels (if needed in future)
    attrs['allergens'] = ''
    attrs['labels'] = ''

    # Try to extract nutritional information and other article details
    try:
        for tr in soup.find(class_='nutrient-table').find_all('tr'):
            if soup.find(class_='nutrient-table').text.split()[0] == "Nährwertinformationen:":
                if 'nutriments' not in attrs:
                    attrs['nutriments'] = []
                attrs['nutriments'].append(re.sub(r'[\s]+', ' ', tr.find('th').text + ':' + tr.find('td').text))
            else:
                if 'Artikelinformationen' not in attrs:
                    attrs['Artikelinformationen'] = []
                attrs['Artikelinformationen'].append(re.sub(r'[\s]+', ' ', tr.find('th').text + ":" + tr.find('td').text))
        if 'nutriments' in attrs:
            attrs['nutriments'] = ' - '.join(attrs['nutriments'])
        if 'Artikelinformationen' in attrs:
            attrs['Artikelinformationen'] = ' - '.join(attrs['Artikelinformationen'])
    except:
        pass

    # Extract the image link
    attrs['Image Link'] = soup.find('img', class_='img-responsive').attrs['src']

    # Combine all product description details into a single string
    attrs['description'] = re.sub(r'[\s]+', ' ', ' '.join([a for a in product_desc]))

    # Check if the product is on sale and extract price information
    if soup.find(class_='oldPrice'):
        attrs['on-sale'] = True
        attrs['sale-price'] = soup.find(name='div', class_='price salesprice').text.strip()
        attrs['price'] = soup.find(name='div', class_='oldPrice').text.strip()
    else:
        attrs['on-sale'] = False
        attrs['price'] = soup.find(name='div', class_='price').text.strip()
        
    # Try to extract unit price
    try:
        attrs['unit-price'] = soup.find(class_='price-note').text.strip().replace('Grundpreis: ', '')
    except:
        pass

    # Optional: Code for extracting ratings using Selenium (commented out)
    # ################################################### FOR RATINGS #################################################################
    # from selenium import webdriver
    # from selenium.webdriver.common.by import By
    # from selenium.webdriver.support.ui import WebDriverWait
    # from selenium.webdriver.support import expected_conditions as EC
    # driver = webdriver.Chrome()
    # driver.get(l)

    # wait = WebDriverWait(driver, 10) # Wait for the element to be present on the page

    # try:
    #     ratings_element = wait.until(EC.presence_of_element_located((By.CLASS_NAME, 'ts-reviewSummary-averageRating')))
    #     ratings_text = ratings_element.text # Get the text content of the element
    #     driver.quit() # Close the browser
    # except:
    #     ratings_text = None
    #     pass
    # attrs['Rating'] = ratings_text
    # ################################################### FOR RATINGS #################################################################

    # Add the link to the product attributes
    attrs['link'] = l
    
    # Append the product attributes to the all_attrs list
    all_attrs.append(attrs)

# Print the list of all product attributes (optional)
# all_attrs

100%|██████████| 7021/7021 [2:28:01<00:00,  1.26s/it]  


[{'id': '',
  'name': 'EDEKA Bio Fettarme H-Milch 1,5% 1L',
  'brand': '',
  'category': 'Lebensmittel',
  'sub-category': 'Kaffee & Tee',
  'allergens': '',
  'labels': '',
  'nutriments': 'Brennwert in kJ:200 - Brennwert in kcal:48 - Fett in g:1,5 - davon gesättigte Fettsäuren in g:1 - Kohlenhydrate in g:5 - davon Zucker in g:5 - Eiweiß in g:3,5 - Salz in g:0,13',
  'Image Link': 'https://www.edeka24.de/out/pictures/generated/product/1/540_540_90/bio_edeka_hmilch_fettarm_15_1l.jpg',
  'description': 'Bio Fettarme H-Milch, 1,5% Fett, ultrahocherhitzt, homogenisiert ultrahocherhitzt | homogenisiert | 1,5% Fett | aus kontrolliert ökologischer Landwirtschaft Hinweis zur Aufbewahrung: Nach dem Öffnen kühl lagern und alsbaldig aufbrauchen. Verantwortliches Lebensmittelunternehmen: EDEKA ZENTRALE Stiftung & Co. KG, D-22291 Hamburg Öko-Kontrollstellencode: AT-BIO-902',
  'on-sale': False,
  'price': '1,35 €',
  'unit-price': '1,35 €/l',
  'link': 'https://www.edeka24.de/Lebensmittel/Kaffee-T

In [7]:
################################# TRANSFERRING VALUES FROM "ARTIKEL INFORMATIONEN(ITEM INFO)" KEY TO THE "DESCRIPTION" KEY############################
for item in all_attrs:
    # Add 'Artikelinformationen' to 'Description' if it exists
    if 'Artikelinformationen' in item:
        # Ensure 'Description' exists and is properly initialized
        if 'description' not in item:
            item['description'] = ''
        
        # Append 'Artikelinformationen' to 'Description'
        item['description'] += ' - ' + item['Artikelinformationen']
        
        # Remove 'Artikelinformationen' key
        del item['Artikelinformationen']
all_attrs

[{'id': '',
  'name': 'EDEKA Bio Fettarme H-Milch 1,5% 1L',
  'brand': '',
  'category': 'Lebensmittel',
  'sub-category': 'Kaffee & Tee',
  'allergens': '',
  'labels': '',
  'nutriments': 'Brennwert in kJ:200 - Brennwert in kcal:48 - Fett in g:1,5 - davon gesättigte Fettsäuren in g:1 - Kohlenhydrate in g:5 - davon Zucker in g:5 - Eiweiß in g:3,5 - Salz in g:0,13',
  'Image Link': 'https://www.edeka24.de/out/pictures/generated/product/1/540_540_90/bio_edeka_hmilch_fettarm_15_1l.jpg',
  'description': 'Bio Fettarme H-Milch, 1,5% Fett, ultrahocherhitzt, homogenisiert ultrahocherhitzt | homogenisiert | 1,5% Fett | aus kontrolliert ökologischer Landwirtschaft Hinweis zur Aufbewahrung: Nach dem Öffnen kühl lagern und alsbaldig aufbrauchen. Verantwortliches Lebensmittelunternehmen: EDEKA ZENTRALE Stiftung & Co. KG, D-22291 Hamburg Öko-Kontrollstellencode: AT-BIO-902',
  'on-sale': False,
  'price': '1,35 €',
  'unit-price': '1,35 €/l',
  'link': 'https://www.edeka24.de/Lebensmittel/Kaffee-T

In [13]:
################ This is an unnecessary line of code, I forgot to make one of the columns names lowercae so I had to write te following ###############

for dictionary in all_attrs:
    if "Image Link" in dictionary:
        dictionary["image-link"] = dictionary.pop("Image Link")

all_attrs

[{'id': '',
  'name': 'EDEKA Bio Fettarme H-Milch 1,5% 1L',
  'brand': '',
  'category': 'Lebensmittel',
  'sub-category': 'Kaffee & Tee',
  'allergens': '',
  'labels': '',
  'nutriments': 'Brennwert in kJ:200 - Brennwert in kcal:48 - Fett in g:1,5 - davon gesättigte Fettsäuren in g:1 - Kohlenhydrate in g:5 - davon Zucker in g:5 - Eiweiß in g:3,5 - Salz in g:0,13',
  'description': 'Bio Fettarme H-Milch, 1,5% Fett, ultrahocherhitzt, homogenisiert ultrahocherhitzt | homogenisiert | 1,5% Fett | aus kontrolliert ökologischer Landwirtschaft Hinweis zur Aufbewahrung: Nach dem Öffnen kühl lagern und alsbaldig aufbrauchen. Verantwortliches Lebensmittelunternehmen: EDEKA ZENTRALE Stiftung & Co. KG, D-22291 Hamburg Öko-Kontrollstellencode: AT-BIO-902',
  'on-sale': False,
  'price': '1,35 €',
  'unit-price': '1,35 €/l',
  'link': 'https://www.edeka24.de/Lebensmittel/Kaffee-Tee/EDEKA-Bio-Fettarme-H-Milch-1-5-1L.html?force_sid=9bigdu1238rk8iavjb0har0mr6',
  'image-link': 'https://www.edeka24.de/

In [15]:
############################################# SAVING ALL PRODUCTS IN A .JSON FILE ################################################

with open('edeka24_all_products.json', 'w', encoding='utf-8') as json_file:
    json.dump(all_attrs, json_file, ensure_ascii=False, indent=4)

In [17]:
############################################# SAVING ALL PRODUCTS IN A .CSV FILE ################################################

# Determine all possible keys
all_keys = set()
for dictionary in all_attrs:
    all_keys.update(dictionary.keys())

# Create a new list of dictionaries with all keys
updated_attrs = []
for dictionary in all_attrs:
    new_dict = {key: dictionary.get(key, '') for key in all_keys}
    updated_attrs.append(new_dict)

# Save the new list of dictionaries to a CSV file
with open("edeka24_all_products.csv", 'w', newline='', encoding='utf-8') as csv_file:
    writer = csv.DictWriter(csv_file, fieldnames=all_keys)
    writer.writeheader()
    writer.writerows(updated_attrs)

In [ ]:
######################################### THIS IS A TRIAL FOR A SINGLE PRODUCT ###############################################

# url = 'https://www.edeka24.de/Lebensmittel/Kaffee-Tee/EDEKA-Bio-Haferdrink-mit-Soja-Barista-1L.html?force_sid=iu3pncg4g1ju97m7v9r8au3v6r'
# resp = requests.get(url, headers=headers)
# soup = BeautifulSoup(resp.text)

# all_attrs = []
# attrs = {}

# attrs['id'] = ''

# try:
#     attrs['name'] = soup.find('h1').text.strip()
# except:
#     all_attrs.append({'link':url})
#     pass

# attrs['brand'] = ''

# product_desc = []
# for listing in soup.find(id='description').find_all(class_='listing'):
#     key = listing.text.strip().split(':')[0]
#     if key == 'Zutatenverzeichnis':
#         attrs["ingredients"] = re.sub(r'[\s]+', ' ', listing.text.replace(key + ':', '').strip())
#     else:
#         product_desc.append(listing.text.strip())

# attrs['category'] =  soup.find('div', class_='breadcrumb').find_all('a')[1].text.strip()
# try:
#     attrs['sub-category'] =  soup.find('div', class_='breadcrumb').find_all('a')[2].text.strip()
# except:
#     pass

# attrs['allergens'] = ''

# attrs['labels'] = ''

# try:
#     for tr in soup.find(class_='nutrient-table').find_all('tr'):
#         if soup.find(class_='nutrient-table').text.split()[0] == "Nährwertinformationen:":
#             if 'nutriments' not in attrs:
#                 attrs['nutriments'] = []
#             attrs['nutriments'].append(tr.find('th').text + ':' + tr.find('td').text)
#         else:
#             if 'Artikelinformationen' not in attrs:
#                 attrs['Artikelinformationen'] = []
#             attrs['Artikelinformationen'].append(tr.find('th').text + ":" + tr.find('td').text)
#     if 'nutriments' in attrs:
#         attrs['nutriments'] = ' - '.join(attrs['nutriments'])
#     if 'Artikelinformationen' in attrs:
#         attrs['Artikelinformationen'] = ' - '.join(attrs['Artikelinformationen'])
# except:
#     pass

# attrs['Image Link'] = soup.find('img', class_='img-responsive').attrs['src']

# attrs['description'] = re.sub(r'[\s]+', ' ', ' '.join([a for a in product_desc]))

# if soup.find(class_='oldPrice'):
#     attrs['on-sale'] = True
#     attrs['sale-price'] = soup.find(name='div', class_='price salesprice').text.strip()
#     attrs['price'] = soup.find(name='div', class_='oldPrice').text.strip()
# else:
#     attrs['on-sale'] = False
#     attrs['price'] = soup.find(name='div', class_='price').text.strip()
    
# try:
#     attrs['unit-price'] = soup.find(class_='price-note').text.strip().replace('Grundpreis: ', '')
# except:
#     pass

# ################################################### FOR RATINGS #################################################################
# #from selenium import webdriver
# #from selenium.webdriver.common.by import By
# #from selenium.webdriver.support.ui import WebDriverWait
# #from selenium.webdriver.support import expected_conditions as EC
# # driver = webdriver.Chrome()
# # driver.get(l)

# # wait = WebDriverWait(driver, 10) # Wait for the element to be present on the page

# # try:
# #     ratings_element = wait.until(EC.presence_of_element_located((By.CLASS_NAME, 'ts-reviewSummary-averageRating')))
# #     ratings_text = ratings_element.text # Get the text content of the element
# #     driver.quit() # Close the browser
# # except:
# #     ratings_text = None
# #     pass
# # attrs['Rating'] = ratings_text
# ################################################### FOR RATINGS #################################################################

# attrs['link'] = url
# all_attrs.append(attrs)

# all_attrs #I saved all products in a list of dictionaries

[{'id': '',
  'name': 'EDEKA Bio Haferdrink mit Soja Barista 1L',
  'brand': '',
  'ingredients': 'Wasser, 10% VOLLKORNHAFER**, 2,0% SOJABOHNEN**, Sonnenblumenöl**, Meersalz. **aus kontrolliert ökologischer Landwirtschaft',
  'category': 'Lebensmittel',
  'sub-category': 'Kaffee & Tee',
  'allergens': '',
  'labels': '',
  'nutriments': 'Brennwert in kJ:210 - Brennwert in kcal:50 - Fett in g:2 - davon gesättigte Fettsäuren in g:0,3 - Kohlenhydrate in g:6,4 - davon Zucker in g:5,1 - Eiweiß in g:1,4 - Salz in g:0,13',
  'Image Link': 'https://www.edeka24.de/out/pictures/generated/product/1/540_540_90/edeka_bio_haferdrink_mit_soja_barista_1l.jpg',
  'description': 'Bio Getränk auf fermentierter Haferbasis mit Sojabasis, ultrahocherhitzt rein pflanzlich | auf Basis von Hafer und Soja | perfektes Aufschäumen für Kaffee oder Cappuccino | von Natur aus laktosefrei | für eine vegetarische und vegane Ernährung geeignet | aus kontrolliert ökologischer Landwirtschaft | Hinweis zur Aufbewahrung: N